In [1]:
!pip install grpcio==1.42.0 tensorflow-serving-api==2.7.0

^C


     ---------------------------------------- 3.3/3.3 MB 3.6 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of tensorboard to determine which version is compatible with other requirements. This could take a while.
  Obtaining dependency information for tensorboard<2.15,>=2.14 from https://files.pythonhosted.org/packages/bc/a2/ff5f4c299eb37c95299a76015da3f30211468e29d8d6f1d011683279baee/tensorboard-2.14.0-py3-none-any.whl.metadata
  Obtaining dependency information for tensorflow-intel==2.14.0 from https://files.pythonhosted.org/packages/cb/90/599c79a248dcae6935331113649de5d75427e320efde21b583648b498584/tensorflow_intel-2.14.0-cp310-cp310-win_amd64.whl.metadata
  Using cached tensorflow_intel-2.14.0-cp310-cp310-win_amd64.whl.metadata (4.8 kB)
  Obtaining dependency information for tensorflow<3,>=2.7.0 from https://files.pythonhosted.org/packages/7c/3c/049400232ee2897d613db9009e42269417166c3f8519d46e5c97b6f9e206/tensorflow-2.15.0-cp310-cp310-win_amd64.whl.metadata
  Using cac


[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
!pip install keras-image-helper


[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
import grpc

import tensorflow as tf

from tensorflow_serving.apis import predict_pb2
from tensorflow_serving.apis import prediction_service_pb2_grpc

In [4]:
host = 'localhost:8500'

channel = grpc.insecure_channel(host) #because run locally and it inside kubernetes

#it's tensorflow thing
#PredictionServiceStub() use to invoking remote service
stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)

In [5]:
from keras_image_helper import create_preprocessor

In [6]:
preprocessor = create_preprocessor('xception', target_size=(299,299))
#url of the image
url = 'http://bit.ly/mlbookcamp-pants'
X = preprocessor.from_url(url)

In [7]:
#turn X into protobuf

def np_to_protobuf(data):
  return tf.make_tensor_proto(data, shape=data.shape)

In [8]:
#prepare the request

pb_request = predict_pb2.PredictRequest()

pb_request.model_spec.name = 'clothing-model' #same with MODEL_NAME
pb_request.model_spec.signature_name = 'serving_default'

#specify the name of input
pb_request.inputs['input_8'].CopyFrom(np_to_protobuf(X))

In [9]:
pb_request

model_spec {
  name: "clothing-model"
  signature_name: "serving_default"
}
inputs {
  key: "input_8"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\350\350\350\275\234\234\034\276\314\314L\276\350\350\350\275\234\234\034\276\314\314L\276\330\330\330\275\224\224\024\276\304\304D\276\270\270\270\275\204\204\004\276\264\2644\276\210\210\210\275\330\330\330\275\234\234\034\276\360\360p\275\310\310\310\275\224\224\024\276\260\2600\275\250\250\250\275\204\204\004\276\240\240\240\274\360\360p\275\330\330\330\275\300\300@\274\320\320P\275\310\310\310\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\250\250\250\275\000\201\200;\220\220\020\275\360\360p\275\300\2600=\000\201\200;\240\240\240\274\220\210\210=\000\341\340<\000\201\200;\260\250\250=\

In [10]:
pb_response = stub.Predict(pb_request, timeout=20.0)

In [11]:
preds = pb_response.outputs['dense_7'].float_val

In [12]:
classes = [
    'dress',
    'hat',
    'longsleeve',
    'outwear',
    'pants',
    'shirt',
    'shoes',
    'skirt',
    't-shirt'
]

In [13]:
dict(zip(classes, preds))

{'dress': -1.87986421585083,
 'hat': -4.75631046295166,
 'longsleeve': -2.359531879425049,
 'outwear': -1.08926522731781,
 'pants': 9.903782844543457,
 'shirt': -2.826179027557373,
 'shoes': -3.648310422897339,
 'skirt': 3.241154909133911,
 't-shirt': -2.612096071243286}